In [1]:
import numpy as np 
import pandas as pd 
import matplotlib.pyplot as plt

#For inline plotting 
%matplotlib inline                 
%config InlineBackend.figure_format = 'svg'

plt.style.use("seaborn-v0_8-dark") 

### A popular Portfolio: S&P500 
-----
S&P 500 is a popular portfolio that actually does not use standard portfolio optimization methods we will discuss later on. However, it is a real-world example of a portfolio that is often used as a proxy for `the financial market`. 

S&P 500 is a cap-weighted index, i.e the weights of the index is proportional to the market capitilization of each company. 

$$ w_i  = \frac{\textrm{market cap}_i}{\sum_{j = 1}^{D} \textrm{market cap}_j} $$

where $D$ number of companies included in the index. Market capitilization typically calculated as 

$$ \textrm{market cap}_i = \textrm{num. of shares}_i \times \textrm{share price}_i $$

The (approximately) 500 companies are chosen by a committee based on companie's minimum market cap, minimum trading volume listed on NYSE or NASDAQ!

### Portfolio Theory
--------

Since stock returns are pretty much random, it does not make too much sense to try to predict the direction of price fluctuations (returns). 

Instead of trying to predict the returns (which can be considered as coint toses), it is better to ask questions like
- How are the coin tosses (returns) are distributed ? 
- Are some coins (returns of different stocks) correlated with other coins? 

Portfolio theory is all about findind answers to these questions to optimally allocate our resources to different stocks in order to maximize gains (cumulative returns) over a specified time horizon. 

#### Risk
-------

Consider the sample mean return (expected return) as your prediction for the future return of a stock price. You will be wrong with this prediction. The concept of risk allow us to quantify how wrong will we be!

Standard deviation of returns will give us a good measure of the risk as it will tell us how much the return will deviate from its expected value. 

In real world, we will be required to choose between stocks that have higher returns but also higher std of returns (risk) or higher volatility of returns. Generically we need to optimize our allocation decisions to minimize the risk while maximazing our profits. 

It is always a trade-off between risk and reward. 

**Diversification for risk reduction**: Assume that we want to choose between two stocks A and B whose returns are identically (Gaussian) distributed (but independent) with a mean $\mu$ and std of $\sigma$: 

$$ r_A, r_B \sim \mathcal{N}(\mu, \sigma^2) $$

If we choose either A and B, our expected return will be $\mu$. If we invest on each equally, our expected return is still $\mu$ however the standard deviation of this portfolio will be reduced as compared to the single asset portfolio's: 

$$ var(r_A) = var(r_B) = \sigma, \quad\quad var(0.5 r_A + 0.5 r_B) = \frac{\sigma^2}{2} \quad\quad \textrm{for} \quad\quad r_A \perp r_B $$

So the variance decreases when we invest in uncorrelated assets that has the same return and risk!

**Toolbox for portfolio Theory**:

- We describe a portfolio with a weight vector $w_i$ of length D which is a measure the proportion of money invested in asset $i = 1,\dots,D$ where $D$ is the number of assets.
- Total weights should some up to unity:

$$ \sum_{i = 1}^{D} w_i = 1$$

- We might have additional constraints such us long only constraint $w_i \geq 0$. 

Portfolio theory is concerned with returns and their correlations described by the covariance matrix:

- returns $R_i$ ( $i = 1,\dots,D$) over a single period of time. 
- Mean return (expected return) of asset $i$: $E(R_i) = \mu_i$
- Covariance of returns: $cov(R_i, R_j) = E((R_i -\mu_i)(R_j-\mu_j)) = \Sigma_{ij}$

The quantities above complete the lowest order statistics of returns in the portfolio from which we can derive the 2-key statistics of the portfolio:

- Expected return of the portfolio: $\mu_p = E(R_p)$ 
- Variance of portfolio return: $\sigma_p^2 = var(R_p)$


$$ \mu_p = \vec{w}. \vec{\mu}$$

$$ \sigma_p^2 = w^T \Sigma w $$



In [2]:
df = pd.read_csv('sp500sub.csv', index_col = 0, parse_dates = True)

df.head()

Open       High        Low      Close  Adj Close   Volume  \
Date                                                                         
2013-01-02  37.919998  38.730000  37.919998  38.340000  38.340000  6483800   
2013-01-03  38.139999  38.299999  37.660000  37.750000  37.750000  3906000   
2013-01-04  37.880001  38.189999  37.619999  38.130001  38.130001  3809300   
2013-01-07  37.810001  38.209999  37.700001  37.939999  37.939999  3632100   
2013-01-08  37.779999  38.200001  37.750000  38.139999  38.139999  3080900   

            Name  
Date              
2013-01-02  ADBE  
2013-01-03  ADBE  
2013-01-04  ADBE  
2013-01-07  ADBE  
2013-01-08  ADBE

In [40]:
df.Name.unique()

array(['ADBE', 'ABBV', 'SBUX', 'MMM', 'ACN', 'AAP', 'AMD', 'NVDA', 'BNTX',
       'IBM', 'ABT', 'SPY', 'AKAM', 'SPL', 'GOOG', 'AFL', 'AES', 'AAPL'],
      dtype=object)

In [57]:
portfolio = ['AFL', 'NVDA', 'BNTX', 'SBUX']

Choosing 4 stocks as diverse as possible, we will work with data with approximately 6 months of time to determine the portfolio allocations. Typically one re-balances the portfolio's periodically over 3,6 and 12 month periods. Over a specified period we want to get all the trading dates in a 6 month range.  

In [58]:
# dates are repeated in the df as different stocks are stack on top of each other

all_dates = df.index.unique().sort_values()

len(all_dates)

2266

In [59]:
# get the indices of a specified start and end date 

start_idx = all_dates.get_loc('2020-01-02')
end_idx = all_dates.get_loc('2020-06-30') 

dates = all_dates[start_idx:end_idx+1]

len(dates)


125

125 roughly corresponding to 252/2 trading days!

In [60]:
# fresh df to store the close prices of stocks of interest 

close_df = pd.DataFrame(index = dates)

for stock in portfolio:
    
    tmp_df = df.loc[dates] # slice the full df for the time of interest
    
    df_stock = tmp_df[tmp_df['Name'] == stock] # corresponding df of the stock in the portfolio
    
    df_stock_close = pd.DataFrame(data = df_stock['Close'].to_numpy(), index = df_stock.index, columns = [stock])
    
    close_df = close_df.join(df_stock_close)
    

In [61]:
close_df.head()

AFL     NVDA       BNTX       SBUX
Date                                                
2020-01-02  53.349998  5.99775  38.500000  89.349998
2020-01-03  52.980000  5.90175  40.049999  88.830002
2020-01-06  52.830002  5.92650  44.580002  88.129997
2020-01-07  52.330002  5.99825  43.340000  87.860001
2020-01-08  52.490002  6.00950  45.099998  88.879997

In [62]:
close_df.isna().sum() # no missing vals 

AFL     0
NVDA    0
BNTX    0
SBUX    0
dtype: int64

In [63]:
# returns df for the portfolio 

returns_df  = (close_df.pct_change() * 100).dropna()

returns_df.head()

AFL      NVDA       BNTX      SBUX
Date                                               
2020-01-03 -0.693531 -1.600596   4.025972 -0.581977
2020-01-06 -0.283121  0.419363  11.310868 -0.788027
2020-01-07 -0.946432  1.210667  -2.781520 -0.306362
2020-01-08  0.305752  0.187555   4.060910  1.160934
2020-01-09  0.019048  1.098261  -4.057645  1.856437

In [64]:
# mean returns and covariance 

mean_returns = returns_df.mean()

cov_df = returns_df.cov()

cov_m  = cov_df.to_numpy()

mean_returns.head()

AFL    -0.202179
NVDA    0.470141
BNTX    0.948275
SBUX   -0.085613
dtype: float64

In [65]:
cov_df

AFL       NVDA        BNTX       SBUX
AFL   23.181389  12.577114   -4.262069  13.170425
NVDA  12.577114  19.747092    8.956850  12.705251
BNTX  -4.262069   8.956850  112.163576   1.184645
SBUX  13.170425  12.705251    1.184645  14.222994

#### Simulating random portfolios from the sample: 
-----

4 asset portfolio: 

In [88]:
# Simulate random portfolio's where weights sum up to 1

N_sim = 25000
D = len(mean_returns)
returns = np.zeros(N_sim)
risks = np.zeros(N_sim)

for i in range(N_sim):
    
    # draw numbers between 0 and 1 from a uniform dist. and normalize them so that they add up to one and finally shuffle 
    rand_w = np.random.random(D) 
    sum_w = sum(rand_w)
    w = np.array([num/sum_w for num in rand_w])
    np.random.shuffle(w)

    ret = mean_returns.dot(w)
    risk = np.sqrt(w.dot(cov_m).dot(w))

    returns[i] = ret 
    risks[i] = risk

3-asset portfolio without SBUX:

In [90]:
# Exclue ONE from the portfolio and simulate 

menage_trois_df = returns_df.drop('SBUX', axis = 1)

# mean returns 

mean_returnsn = menage_trois_df.mean()

# covariance matrix 

cov_dfn = menage_trois_df.cov()
cov_mn = cov_dfn.to_numpy()

# Simulate random portfolio's where weights sum up to 1

N_sim = 25000
Dn = len(mean_returnsn)
returnsn = np.zeros(N_sim)
risksn = np.zeros(N_sim)

for i in range(N_sim):
    
    # draw numbers between 0 and 1 from a uniform dist. and normalize them so that they add up to one and finally shuffle 
    rand_w = np.random.random(Dn) 
    sum_w = sum(rand_w)
    w = np.array([num/sum_w for num in rand_w])
    np.random.shuffle(w)

    ret = mean_returnsn.dot(w)
    risk = np.sqrt(w.dot(cov_mn).dot(w))

    returnsn[i] = ret 
    risksn[i] = risk

Single Asset Portfolios:

In [91]:
# single asset returns and risks 

s_asset_returns = np.zeros(D)
s_asset_risks =  np.zeros(D)

for i in range(D):

    ret = mean_returns[i]
    risk = np.sqrt(cov_m[i,i]) # if you invest in single asset, risk is just individual risk of each 

    s_asset_returns[i] = ret
    s_asset_risks[i] = risk

Min/Max Return portfolios:

In [92]:
from scipy.optimize import linprog as lp

# min-max return and its corresponding risk for the full portfolio 
# only optimizing mean returns without optimizing risk

D = len(mean_returns)

A_eq = np.ones((1,D)) # D dimensional transpose identity vector 
b_eq = np.ones(1)

# bounds on w

bounds = [(0.01,0.99)]*D # put at least 0.01 percent to an asset so that we have a full portolio 

res_min = lp(mean_returns, A_eq = A_eq, b_eq = b_eq, bounds=bounds)
res_max = lp(-mean_returns, A_eq = A_eq, b_eq = b_eq, bounds=bounds)

# min/max returns and the corresponding risks of the sample

min_weights = res_min.x
min_return = res_min.fun 

max_weights = res_max.x
max_return = - res_max.fun

min_risk = np.sqrt(min_weights.dot(cov_m).dot(min_weights))
max_risk = np.sqrt(max_weights.dot(cov_m).dot(max_weights))

Efficient Frontier:

In [94]:
from scipy.optimize import minimize

# get the efficient frontier between max and min returns optimizing (minimizing) variance using minimize from scipy 

N = 200

# define a grid of return values to iterate 

#kini = min_return; 
#kfin = max_return; 

target_returns = np.linspace(min_return, max_return, num = N)# Generate an empty list an fill it iteratively by evaluating integral below

#for i in np.arange(1,N+1):
#    target_returns.append(kini*(kfin/kini)**((i-1)/(N-1)))


def portfolio_var(w): # the function to be optimized

    return w.dot(cov_m).dot(w)

def target_return_constraint(w, target): # we will iterate through target return within the min max we identified above

    return w.dot(mean_returns) - target 

def weight_constraint(w):

    return w.sum() - 1

# constraints to input into minimize function 

constraints = [{'type': 'eq', 'fun':  target_return_constraint, 'args': [target_returns[0]]}, {'type': 'eq', 'fun': weight_constraint}]

opt_risks = []

for target in target_returns:

    # set the target constraint for a given return between min and max

    constraints[0]['args'] = [target]

    res = minimize(fun = portfolio_var, x0 = np.ones(D)/D, method = 'SLSQP', constraints = constraints, bounds = bounds)

    opt_risks.append(np.sqrt(res.fun))

    if res.status != 0:

        print('Problem with optimization')

Global Minimum Variance and Max Sharpe Ratio Portfolios:

In [95]:
# Get the Global minimum variance portfolio and its corresponding return

mvp_res = minimize(fun = portfolio_var, x0 = np.ones(D)/D, method = 'SLSQP', constraints = {'type': 'eq', 'fun': weight_constraint}, bounds = bounds)

mvp_risk = np.sqrt(mvp_res.fun)
mvp_weights = mvp_res.x

mvp_return = mvp_weights.dot(mean_returns)

# Get the portfolio with maximum Sharpe Ratio 

def sharpe_ratio(w, rf = 0): # assume risk free rate to be zero 

    mean = w.dot(mean_returns)
    std = np.sqrt(w.dot(cov_m).dot(w))
    return -(mean-rf)/std  # negate so that we maximize

max_sr_res = minimize(sharpe_ratio, x0 = np.ones(D)/D, method = 'SLSQP', constraints = {'type': 'eq', 'fun': weight_constraint}, bounds = bounds)

max_sr, max_sr_weights = - max_sr_res.fun, max_sr_res.x   

max_sr_risk = np.sqrt(max_sr_weights.dot(cov_m).dot(max_sr_weights))
max_sr_ret = mean_returns.dot(max_sr_weights)

In [96]:
# visualize the Markowitz bullet 
fig, axes = plt.subplots(figsize = (12,6))

# plot full portfolios and the ones without DOGE
axes.scatter(risks, returns, alpha = 0.07, c = 'blue')
#axes.scatter(risksn, returnsn, alpha = 0.05, c = 'brown')

# min/max return portfolios given that each weight is nonzero (e.g more than 0.005) so that the portfolio contains all of the assests
axes.scatter(min_risk, min_return, c = 'black', marker = 'x', label = 'min_return: 0.01 < w < 1')
axes.scatter(max_risk, max_return, c = 'brown', marker = 'x', label = 'max_return: 0.01 < w < 1')

# efficient frontier 
axes.plot(opt_risks, target_returns, c = 'black', alpha = 0.6, label = 'Efficient frontier')

# global minimum variance portfolio 
axes.scatter(mvp_risk, mvp_return, c = 'gray', alpha = 0.9, label = 'Global minimum risk portfolio')

# max Sharpe ratio portfolio 
axes.scatter(max_sr_risk, max_sr_ret, c = 'darkblue', label = 'Max sharpe ratio portfolio')


# single asset portfolios
axes.scatter(s_asset_risks[0], s_asset_returns[0], c = 'magenta', label = 'Only AFL')
axes.scatter(s_asset_risks[1], s_asset_returns[1], c = 'green', label = 'Only NVDA')
axes.scatter(s_asset_risks[2], s_asset_returns[2], c = 'orange', label = 'Only BNTX')
axes.scatter(s_asset_risks[3], s_asset_returns[3], c = 'red', label = 'Only SBUX')

axes.grid()
axes.legend()
axes.set_xlabel('Risk')
axes.set_ylabel('Percentage Return')


Text(0, 0.5, 'Percentage Return')

Biontech `BNTX` is the most risky asset which also offers highest returns. On the contrary `SBUX` is the least risky asset with small returns! Notice that staying with the same risk level we can potentially obtain higher returns. As clear from the most risk and the least risky asses, there is a trade-off between mean and variance! 

Top part of the Markowitz bullet (with positive returns) gives us the `Efficient Frontier` exploits this mean-variance trade-off to give us the efficient portfolios because for each of these portfolios given their expected return there is no better portfolio that gives you less risk. In other words, along the efficient frontier for a desired risk there is no other portfolio that can provide you a higher return. 

#### Portfolio with a risk-free asset and Tangency Portfolio
----

What if we split our investment into both a risk free asset and the portfolio with the maximum sharpe ratio? In this case we get a line that connects the risk free point (P1) with the maximum sharp ratio portfolio (P2)! 

In the graph above the point with zero risk corresponds to the case when we invest 100 percent on the risk free asset such as a T-bill. 

The in between points is also achievable! These points corresponds to higher return with the same risk, with respect to the portfolio's that lie below the efficient frontier ( e.g risky assets). 

The line that connects P1 and P2 (and actually extends further beyond P2) is tangent to the point where we find the maximum sharpe ratio. This implies that all the points on this line has the same Sharpe Ratio which is the slope of the line itself!!!

In summary any portfolio constructed on this line is a portfolio out of portfolios. More concretely, 


- Tangency portfolio:

$$ \textrm{return:}\, R_T, \quad E(R_T) = \mu_T, \quad var(R_T) = \sigma_T^2 $$

- The risk-free asset: 

$$ \textrm{return:}\, r_f, \quad E(r_f) = r_f, \quad var(r_f) = 0 $$

The new portfolio constructed out of these assests: 

$$ R_p = w_T R_T + (1-w_T) r_f  $$

The expected return of the new portfolio is then given by 

$$ E(R_p) = \mu_p = w_T \mu_T + (1-w_T) r_f$$

whereas the variance of the new portfolio is

$$ var(R_p) = var(w_T R_T) + var((1-w_T)r_f) = w_T^2 \sigma_T^2 $$

since the risk free asset is independent from the tangency portfolio. This tells us that the risk associated with this portfolio is linearly related to the risk associated with the tangency portfolio, which is smaller than the latter: 

$$ \sigma_p = w_T \sigma_T \quad \longrightarrow \quad w_T = \frac{\sigma_p}{\sigma_T}$$

Using this we can obtain the sharpe ratio of the new portfolio: 

$$ \textrm{Sharpe}_p = \frac{\mu_p}{\sigma_p} = \frac{\mu_T}{\sigma_T} + \left(\frac{1}{\sigma_p} - \frac{1}{\sigma_T}\right)r_f$$

or equivalently

$$ \textrm{Sharpe}_p = \frac{\mu_p}{\sigma_p} = \frac{\mu_T - r_f}{\sigma_T} + \frac{r_f}{\sigma_p}   $$

Notice that the expected return of the portfolio is given by 

$$ \mu_p = \frac{\mu_T - r_f}{\sigma_T} \sigma_p + r_f$$

which has the expected linear form in $\sigma_p$ with $r_f$ as the intercept. The slope of this line is just the sharpe ratio of the tangency portfolio! This simply means that any portfolio constructed using the tangency portfolio and the risk free asset has this specific sharpe ratio! In particular, arranging the equation above we have 

$$ \frac{\mu_p - r_f}{\sigma_p} = \frac{\mu_T - r_f}{\sigma_T} $$

so that the sharpe ratio of the mixed portfolio is always equivalent to the sharpe ratio of the tangency portfolio!

In [97]:
# tangent line 

x1 = 0 
y1 = 0.05 # risk free rate

x2 = max_sr_risk
y2 = max_sr_ret


# visualize the Markowitz bullet 
fig, axes = plt.subplots(figsize = (12,6))

# plot full portfolios and the ones without DOGE
axes.scatter(risks, returns, alpha = 0.07, c = 'blue')
#axes.scatter(risksn, returnsn, alpha = 0.05, c = 'brown')

# min/max return portfolios given that each weight is nonzero (e.g more than 0.005) so that the portfolio contains all of the assests
axes.scatter(min_risk, min_return, c = 'black', marker = 'x', label = 'min_return: 0.01 < w < 1')
axes.scatter(max_risk, max_return, c = 'brown', marker = 'x', label = 'max_return: 0.01 < w < 1')

# efficient frontier 
axes.plot(opt_risks, target_returns, c = 'black', alpha = 0.6, label = 'Efficient frontier')

# max Sharpe ratio portfolio 
axes.scatter(max_sr_risk, max_sr_ret, c = 'darkblue', label = 'Max sharpe ratio portfolio')

# plot of the tangent line 

axes.plot([x1,x2],[y1,y2], color = 'red')


axes.grid()
axes.legend()
axes.set_xlabel('Risk')
axes.set_ylabel('Percentage Return')


Text(0, 0.5, 'Percentage Return')

### Capital Asset Pricing Model (CAPM)
----

We have pretty much derived all the theory behind CAPM. We just need to rename some variables for the most part. 

We established earlier that portfolio with the maximum Sharpe Ratio is the tangency portfolio which is also called Market Portfolio, the line that connect risk free asset with the Market Portfolio (and potentially extends beyond) is the Capital Market Line (CML)!

- The basic logic behind this renaming relies on the Efficient Market Hypothesis (EMH) where it is assumed that every investor has the same data and every investor is a mean-variance optimizer. Therefore they have to choose the tangency portfolio with some mixture of the risk-free asset, because there is no better portfolio!

A scenario application of CML: 

Suppose you are considering investing on a project to build Silicon Valley's next disruptive technology. Suppose the share price of this tech today is $1000 and expected to be worth $1200 in one year with volatility %20 percent. Current risk-free rate is $r_f = 3\%$. The expected return on the market portfolio is $15\%$ with volatility $\%10$ percent. Is it worth considering this investment? 

Answer: 

Expected return on this investment $\mu = 1200/1000 - 1 = 20 \%$ 

But according to the CAPM if we take on a risk level of 20 percent, we should expect the return to be 

$$ r_f + \frac{\mu_M - r_f}{\sigma_M} \sigma = 3 + (15-3) 2 = 27 \% $$

So we can conclude that this investment is not worth considering! In other words, according to the sharpe ratio of the market we should demand more reward on an investment with 20 percent volatility.  



Another interesting points about CAPM is the security Market Line (SML)

$$ \mu_i - r_f = \beta_i (\mu_M - r_f) $$

which is a linear regression of an asset $i$'s excess return on the Market's excess return. The left hand side is also called the risk premium, where as the corresponding term on the right hand side is the market premium.

$\beta_i$ tells us how much the asset $i$ moves relative to the market. 

If

$\beta > 1$, we call it an aggressive investment (willing to take on more risk in return for more reward). $\beta = 1$, we call the asset average risk, if $\beta < 1$, we call it not aggressive. So in CAPM, beta becomes the measure of risk! It is actually called the systematic risk or market risk as it depends on the market!

Plotting the expected return of an asset with respect to $\beta$ (e.g systematic risk) gives the security market line. According to the CAPM, all assets should fall on this line otherwise, the asset is mispriced. This will help investors for investment decisions : if undervalued buy, else sell!

**Security Characteristic Line**: Adds a time component to the SML and remove the expected values 

$$ R_i (t) - r_f(t) = \beta_i (R_M(t) - r_f(t)) + \epsilon_i(t)$$ 

or rewriting the excess returns with a single symbol: 

$$  R'_i (t) = \beta_i R'_M(t) + \epsilon_i(t) $$ 

Inlcuding $\alpha$: 

- According to the CAPM, expected value of $\alpha$ is 0 
- Including $\alpha$ allows for the possibility of mispricing that can not be attributed to the market 

$$  R'_i (t) = \alpha_i + \beta_i R'_M(t) + \epsilon_i(t)  $$

Intepretation of $\alpha$: 

- If $\alpha \neq 0$, the security is mispriced 
- If $\alpha > 0$, the security is mispriced 
    - The returns have been to large on average
    - This is a buy signal 
- If we reject the null hypotesis that $\alpha = 0$, we have only shown that the security was mispriced in the past which is not guaranteed in the future!

**Summary of CAPM**: 

- The CAPM is a wrong but a useful model

- Its assumptions: 
    - Markets are in equilibrium (supply equals demand)
    - Every investor has the same forecasts of returns and risks 
    - Every investor is a mean-variance optimizer (holds a combination of tangency portfolio and risk-free asset)

- The CAPM is still a useful pricing model, and is the basis for more advanced techniques such as 

   - Fama and French 3-factor model: which includes factor that the Market itself (CAPM is a single factor model)

      $$ R'_i (t) = \alpha_i + \beta_1 R'_M(t) + \beta_2 SMB(t) + \beta_3 HML(t) + \epsilon_i(t) $$

   - Statistical factor models (PCA, Factor Analysis-Unsupervised ML): these are unsupervised machine learning methods which try to figure out what the factors might be without you having to assing them explicitly. 

     $$ R'_i (t) = \alpha_i + \beta_1 f_1 + \beta_2 f_2 + \dots +  \beta_K f_K + \epsilon_i $$

### Problems with Modern Portfolio Theory
-----

- How do we actually know the expected return/covariance of the asset universe? (We don't)
  
  - This lack of knowledge has a detrimental effect on portfolio optimization. Two general strategies one can apply in this context is 
    1. Estimate of the expected return and covariance of returns based on historical returns: For example using the simple moving average or the exponentially weighted moving average. 
    2. Use ML to predict expected return and volatility may be in the future utilizing all sorts of data. 


### A more mature view of the problem 
----

- If you are from ML, your strategy is how to be more accurate? 
- But it is very difficult to predict things accurately, you will certainly be wrong which is almost guaranteed! 
- The more correct approach is to think ways we can mitigate the effects of being wrong: How can we mitigate the effects of being wrong? 

**Several strategies that we can use to address these questions**:

1. Global Minimum Variance Portfolio: recall that it minimizes variance without any regard to the return

    - It turns out that sample return is much less stable than sample covariance
    - An interesting consequence is that it can acually lead to good returns: [link](https://papers.ssrn.com/sol3/papers.cfm?abstract_id=1585031)

2. Setting bounds on portfolio weights

   - E.g don't allowing short-selling and limiting maximum weight of an asset

3. Bootstrapping: Supposing that our sample data is the true data, we resample from the sample by drawing sample with replacement allowing of course duplicates and doing this resampling $B \gg 1$ times. 

    - Each time calculate the 'optimal' portfolio
    - Then (using the original smaple as the ground truth) check how wrong the portfolios from the resamples are. 

4. Shrinkage Estimation

   - General idea: Unbiased estimates of mean/covariance are error-prone, so mix them with more stable estimates 
   - Should seem intuitive if you are familiar with Bayesian Machine Learning or MAP(Maximum A posteriori) estimation 

   $$ \hat{\Sigma}_{shrink} = \delta F + (1-\delta) \hat{\Sigma}_{unbiased} $$

   where F is highly structered estimator. See e.g the [link](https://repositori.upf.edu/bitstream/handle/10230/560/691.pdf?sequence=1)

5. A commonly accepted method of estimating expected returns: [Black-Litterman method](
https://faculty.fuqua.duke.edu/~charvey/Teaching/BA453_2006/Idzorek_onBL.pdf).
